# Data imbalance analysis
## Comparing the impact of dataset imbalance on classification performance metrics
In this notebook, we are going to explore how data imbalance affect classification scores on four different tasks, which have been chosen to exemplify typical use cases of ML analysis in neuroscience. To keep it simple, we will focus on binary classification problems (0 vs 1).

The four tasks are :
1. Synthetic data
2. EEG alpha oscillations (resting-state Eyes-Closed vs Eyes-Open)
3. MEG alpha oscillations (auditory vs visual stimulation)
4. MEG alpha oscillations (faces vs scrambled) 

In these tasks, we will observe the effect of data imbalance on 4 different performance metrics :   
1. Decoding Accuracy (Acc)  
2. Area Under the Curve (AUC)
3. F1
4. Balanced Accuracy (BAcc)

Finally, a few parameters of the classification pipeline must be kept in mind as they can also differentially impact performance on imbalanced data. Namely :
- Dataset size
- Classifier type
    - Support Vector Machine (SVM)
    - Linear Discriminant Analysis (LDA)
    - Logistic Regression (LR)
    - Random Forest (RF)
- Cross-validation scheme
    - K-Fold, k=5
    - Stratified K-Fold
    - Group K-Fold

## Imports
First, we start by importing functions from the provided toolbox as well as some useful plotting functions.

In [15]:
from imbalance.pipeline import Pipeline
from imbalance.viz import metric_balance, data_distribution, plot_different_cvs, plot_different_n
from imbalance.data import eegbci, gaussian_binary
from joblib import Parallel, delayed
from sklearn.model_selection import (
    KFold,
    StratifiedKFold,
    StratifiedGroupKFold,
)
import os
import numpy as np
import matplotlib.pyplot as plt
import string
from copy import deepcopy
import warnings
warnings.simplefilter("ignore", RuntimeWarning)

plt.style.use('seaborn')

## Task 1 : Synthetic data
For that first classification task, we will generate data from two gaussian distributions, with means of 0 and 2.

In [3]:
pls = []

def run(distance):
    # generate random data
    x, y, groups = gaussian_binary(n_samples_per_class=500, mean_distance=distance)
    # run the pipeline
    pl = Pipeline(
        x,
        y,
        groups,
        dataset_balance=np.linspace(0.1, 0.9, 25),
        classifiers=["lr", "lda", "svm", "rf"],
        n_permutations=100,
        n_init=10,
    )
    pl.evaluate()
    return deepcopy(pl)



pls = Parallel(n_jobs=3)(delayed(run)(dist) for dist in [0, 1, 3])

fitting classifiers: 100%|██████████| 1000/1000 [27:14<00:00,  1.63s/it, size=1, balance=0.9, classifier=RandomForestClassifier]       

In [4]:
# generate random data
x, y, groups = gaussian_binary(n_samples_per_class=1500, mean_distance=1)
# run the pipeline
pl_nsamples = Pipeline(
    x,
    y,
    groups,
    dataset_balance=np.linspace(0.1, 0.9, 25),
    classifiers=["svm"],# "rf"]
    n_permutations=0,
    n_init=10,
    dataset_size=(0.1, 0.33, 1),
)
pl_nsamples.evaluate()

fitting classifiers:   0%|                             | 0/750 [00:00<?, ?it/s, size=0.1, balance=0.1, classifier=SVC]


fitting classifiers: 100%|█████████████████████| 750/750 [03:41<00:00,  3.39it/s, size=1, balance=0.9, classifier=SVC]


In [5]:

pls_crossvals = {}
cv_names = ["KFold", "Stratified"]#, "Stratified Group"]
cvs = [KFold(n_splits=5), StratifiedKFold(n_splits=5)]#, StratifiedGroupKFold(n_splits=5)]
# generate random data
x, y, groups = gaussian_binary(n_samples_per_class=50, n_groups=5, mean_distance=1)
# run the pipeline
for idx_cv, cross_val in enumerate(cvs):
    pl = Pipeline(
        x,
        y,
        groups,
        dataset_balance=np.linspace(0.1, 0.9, 25),
        classifiers=["lr", "lda", "svm", "rf"],
        n_permutations=1,
        n_init=40,
        cross_validation=cross_val,
    )
    pl.evaluate()
    pls_crossvals[cv_names[idx_cv]] = deepcopy(pl)
    




fitting classifiers:   0%|               | 0/4000 [00:00<?, ?it/s, size=1, balance=0.1, classifier=LogisticRegression]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predic

/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
fitting classifiers:   0%| | 7/4000 [00:00<04:50, 13.75it/s, size=1, balance=0.133, classifier=RandomForestClassifier]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes n

fitting classifiers:   2%| | 91/4000 [00:06<04:02, 16.11it/s, size=1, balance=0.833, classifier=RandomForestClassifier/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:   2%| | 95/4000 [00:06<04:45, 13.66it/s, size=1, balance=0.867, classifier=RandomForestClassifier/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning:

fitting classifiers:   5%|▏  | 192/4000 [00:10<02:03, 30.81it/s, size=1, balance=0.867, classifier=LogisticRegression]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:   5%| | 193/4000 [00:10<02:03, 30.81it/s, size=1, balance=0.867, classifier=LinearDiscriminantAna/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:   5%|▊                 | 194/4000 [00:10<02:03, 30.81it/s, size=1, balance=0.867, classifier=SVC]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
f

fitting classifiers:   7%|█▍                  | 286/4000 [00:12<01:50, 33.71it/s, size=1, balance=0.8, classifier=SVC]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:   7%| | 287/4000 [00:12<01:50, 33.71it/s, size=1, balance=0.8, classifier=RandomForestClassifier]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:   7%| | 291/4000 [00:13<01:49, 33.92it/s, size=1, balance=0.833, classifier=RandomForestClassifie/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
f

...

fitting classifiers:  90%|▉| 3595/4000 [02:03<00:13, 30.38it/s, size=1, balance=0.867, classifier=RandomForestClassifi/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:  90%|███▌| 3596/4000 [02:03<00:13, 30.45it/s, size=1, balance=0.9, classifier=LogisticRegression]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:  90%|▉| 3597/4000 [02:03<00:13, 30.45it/s, size=1, balance=0.9, classifier=LinearDiscriminantAnal/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
f

fitting classifiers:  92%|▉| 3677/4000 [02:06<00:10, 30.50it/s, size=1, balance=0.733, classifier=LinearDiscriminantAn/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:  92%|▉| 3679/4000 [02:06<00:10, 30.50it/s, size=1, balance=0.733, classifier=RandomForestClassifi/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:  92%|▉| 3687/4000 [02:06<00:10, 30.00it/s, size=1, balance=0.8, classifier=RandomForestClassifier/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
f

fitting classifiers:  93%|▉| 3711/4000 [02:07<00:09, 30.32it/s, size=1, balance=0.167, classifier=RandomForestClassifi/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
fitting classifiers:  95%|█▉| 3792/4000 [02:10<00:06, 30.97it/s, size=1, balance=0.867, classifier=LogisticRegression]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1999: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
fitting classifiers:  95%|▉| 3793/4000 [02:10<00:06, 30.97it/s, size=1, balance=0.867, classifier=LinearDiscriminantAn/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classif

fitting classifiers:  95%|▉| 3809/4000 [02:10<00:06, 28.95it/s, size=1, balance=0.167, classifier=LinearDiscriminantAn/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
fitting classifiers:  95%|████████████████▏| 3810/4000 [02:10<00:06, 28.95it/s, size=1, balance=0.167, classifier=SVC]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
fitting classifiers:  95%|▉| 3811/4000 [02:10<00:06, 28.95it/s, size=1, balance=0.

fitting classifiers:  98%|█▉| 3904/4000 [02:13<00:03, 30.68it/s, size=1, balance=0.133, classifier=LogisticRegression]/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1592: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
fitting classifiers:  98%|▉| 3905/4000 [02:13<00:03, 30.68it/s, size=1, balance=0.133, classifier=LinearDiscriminantAn/home/hyruuk/anaconda3/envs/imbalance/lib/python3.8/site-packages/sklearn/metrics/

In [6]:
# generate random data
x, y, groups = gaussian_binary(n_samples_per_class=500, mean_distance=1)
# run the pipeline
pl_balance = Pipeline(
    x,
    y,
    groups,
    dataset_balance=np.linspace(0.1, 0.9, 25),
    classifiers=["svm"],# "rf"]
    n_permutations=0,
    n_init=10,
    single_balanced_split=True,
)
pl_balance.evaluate()

fitting classifiers: 100%|█████████████████████| 250/250 [00:13<00:00, 18.55it/s, size=1, balance=0.9, classifier=SVC]


In [9]:
# visualize the result
fig, axes = plt.subplots(7, 3, figsize=(20, 30), dpi=300, gridspec_kw=dict(height_ratios=[1, 1, 1, 1, 1, 0.1, 1]))
figtitle = "Synthetic data"
#fig.suptitle(figtitle, fontsize=25)
classifiers=["lr", "lda", "svm", "rf"]

show_leg_distrib=True
show_leg_metric=True
for ax_idx,ax in enumerate(axes.flat):
    if ax_idx not in [15,16,17]:
        
        ax.text(-0.1, 1.05, string.ascii_uppercase[ax_idx], transform=ax.transAxes, 
                size=20, weight='bold')
    if ax_idx in [0,1,2]:
        data_distribution(pls[ax_idx], ax=ax, show=False, show_leg=show_leg_distrib)
        show_leg_distrib=False
    elif ax_idx < 15:
        metric_balance(pls[ax_idx%3], ax=ax, show=False, classifier=classifiers[(ax_idx-3)//3], show_leg=show_leg_metric)
        show_leg_metric = False
    elif ax_idx == 15+3:
        plot_different_n(pl_nsamples, ax=ax, show=False, classifier="svm", show_leg=True, metric="accuracy")
    elif ax_idx == 16+3:
        plot_different_cvs(pls_crossvals, ax=ax, show=False, classifier="svm", show_leg=True, metric="accuracy")
    elif ax_idx == 17+3:
        metric_balance(pl_balance, ax=ax, show=False, classifier="svm", show_leg=True)
        
        
cols = ['Distance = 0', 'Distance = 1', 'Distance = 3']
rows = ["LDA", "LR", "SVM", "RF", "Secondary parameters"]

for ax, col in zip(axes[0], cols):
    ax.set_title(col)

for ax, row in zip(axes[:,0], rows):
    ax.set_ylabel(row, rotation=0, size='large')

fig.tight_layout()
plt.show()
    

In [23]:
# visualize the result
fig, axes = plt.subplots(7, 3, figsize=(20, 30), dpi=300, 
                         gridspec_kw=dict(height_ratios=[1, 1, 1, 1, 1, 0.1, 1]))
figtitle = "Synthetic data"
#fig.suptitle(figtitle, fontsize=25)
classifiers=["lr", "lda", "svm", "rf"]
spot_names = string.ascii_uppercase[:18]

show_leg_distrib=True
show_leg_metric=True
spot_idx = 0
for dist_idx, dist in enumerate([0,1,3]):
    for ax_idx, ax in enumerate(axes[:,dist_idx]):
        if ax_idx == 0:
            data_distribution(pls[dist_idx], ax=ax, show=False, show_leg=show_leg_distrib)
            show_leg_distrib=False
        elif ax_idx < 5:
            metric_balance(pls[dist_idx], ax=ax, show=False, classifier=classifiers[ax_idx-1], show_leg=show_leg_metric)
            show_leg_metric = False
        elif ax_idx == 6:
            if dist_idx == 0:
                plot_different_n(pl_nsamples, ax=ax, show=False, classifier="svm", show_leg=True, metric="accuracy")
            if dist_idx == 1:
                plot_different_cvs(pls_crossvals, ax=ax, show=False, classifier="svm", show_leg=True, metric="accuracy")
            if dist_idx == 2:
                metric_balance(pl_balance, ax=ax, show=False, classifier="svm", show_leg=True)
        if ax_idx != 5:
            ax.text(-0.1, 1.05, spot_names[spot_idx], transform=ax.transAxes, 
                size=20, weight='bold')
            spot_idx += 1
        if ax_idx == 5:
            ax.axis('off')
            
        
cols = ['Distance = 0', 'Distance = 1', 'Distance = 3']
rows = ["LDA", "LR", "SVM", "RF", "Secondary parameters"]

for ax, col in zip(axes[0], cols):
    ax.set_title(col)

for ax, row in zip(axes[:,0], rows):
    ax.set_ylabel(row, rotation=0, size='large')

fig.tight_layout()
plt.show()
    

In [ ]:
axes[:,0]

In [ ]:
metrics=[ "roc_auc","accuracy", "f1", "balanced_accuracy"]
fig, axes = plt.subplots(2, 2, figsize=(20, 10))

#pls_crossvals_light = pls_crossvals[:2]
for ax_idx,ax in enumerate(axes.flat):
    plot_different_cvs(pls_crossvals, ax=ax, show=False, classifier="svm", show_leg=True, metric=metrics[ax_idx])

In [ ]:
plot_different_n(pl_nsamples, show=False, classifier="svm", show_leg=True, metric="accuracy")

## Task 2 : EEG analysis

In [10]:
#pipeline_path="../imbalance/data/eeg.pickle"
features_path ="../imbalance/data/eeg_features.npy"

# load or generate dataset
if not os.path.isfile(features_path):
    x, y, groups = eegbci('../imbalance/data',roi=lambda x: x[0] in ['P','O'])
    np.save(features_path,dict(x=x, y=y, groups=groups))
else:
    features = np.load(features_path,allow_pickle=True).item()
    x, y, groups = features["x"] , features["y"] , features["groups"]

In [13]:
pl = Pipeline(
    x,
    y,
    groups,
    dataset_balance=np.linspace(0.1, 0.9, 25),
    classifiers=["lda","svm","lr", "rf"]
)
# fit and evaluate classifiers on dataset configurations
pl.evaluate()

pl_nsamples = Pipeline(
    x,
    y,
    groups,
    dataset_balance=np.linspace(0.1, 0.9, 25),
    classifiers=["svm"],# "rf"]
    n_permutations=0,
    n_init=10,
    dataset_size=(0.1, 0.33, 1),
)
pl_nsamples.evaluate()


fitting classifiers:   0%|       | 0/1000 [00:00<?, ?it/s, size=1, balance=0.1, classifier=LinearDiscriminantAnalysis]
fitting classifiers:   0%| | 1/1000 [00:06<1:52:47,  6.77s/it, size=1, balance=0.1, classifier=LinearDiscriminantAnaly
fitting classifiers:   0%| | 4/1000 [00:39<2:57:45, 10.71s/it, size=1, balance=0.1, classifier=RandomForestClassifier]
fitting classifiers:   0%| | 4/1000 [00:39<2:57:45, 10.71s/it, size=1, balance=0.133, classifier=LinearDiscriminantAna
fitting classifiers:   0%| | 5/1000 [00:44<2:26:55,  8.86s/it, size=1, balance=0.133, classifier=LinearDiscriminantAna
fitting classifiers:   1%|   | 7/1000 [01:03<2:26:03,  8.83s/it, size=1, balance=0.133, classifier=LogisticRegression]
fitting classifiers:   1%| | 7/1000 [01:03<2:26:03,  8.83s/it, size=1, balance=0.133, classifier=RandomForestClassifie
fitting classifiers:   1%| | 8/1000 [01:19<3:01:31, 10.98s/it, size=1, balance=0.133, classifier=RandomForestClassifie
fitting classifiers:   1%| | 8/1000 [01:19<3:01

fitting classifiers:   4%|  | 35/1000 [09:11<5:56:03, 22.14s/it, size=1, balance=0.367, classifier=LogisticRegression]
fitting classifiers:   4%| | 35/1000 [09:11<5:56:03, 22.14s/it, size=1, balance=0.367, classifier=RandomForestClassifi
fitting classifiers:   4%| | 36/1000 [09:30<5:41:24, 21.25s/it, size=1, balance=0.367, classifier=RandomForestClassifi
fitting classifiers:   4%| | 36/1000 [09:30<5:41:24, 21.25s/it, size=1, balance=0.4, classifier=LinearDiscriminantAnal
fitting classifiers:   4%| | 37/1000 [09:36<4:26:29, 16.60s/it, size=1, balance=0.4, classifier=LinearDiscriminantAnal
fitting classifiers:   4%|▏   | 39/1000 [11:08<7:30:03, 28.10s/it, size=1, balance=0.4, classifier=LogisticRegression]
fitting classifiers:   4%| | 39/1000 [11:08<7:30:03, 28.10s/it, size=1, balance=0.4, classifier=RandomForestClassifier
fitting classifiers:   4%| | 40/1000 [11:30<6:57:49, 26.11s/it, size=1, balance=0.4, classifier=RandomForestClassifier
fitting classifiers:   4%| | 40/1000 [11:30<6:57

KeyboardInterrupt: 

In [ ]:
# visualize the result
fig, axes = plt.subplots(2, 3, figsize=(20, 10))
figtitle = "EEG data"
#fig.suptitle(figtitle, fontsize=25)
classifiers=["lr", "lda", "svm", "rf"]

for ax_idx,ax in enumerate(axes.flat):
    ax.text(-0.1, 1.05, string.ascii_uppercase[ax_idx], transform=ax.transAxes, 
            size=20, weight='bold')
    if ax_idx == 0:
        data_distribution(pl, ax=ax, show=False)
    elif ax_idx < 6:
        metric_balance(pl, ax=ax, show=False, classifier=classifiers[ax_idx-1])
    elif ax_idx == 6:
        plot_different_n(pl_nsamples, ax=ax, show=False, classifier="svm", show_leg=True, metric="accuracy")

## Task 3 : MEG 1

In [ ]:
# visualize the result
fig, axes = plt.subplots(2, 3, figsize=(20, 10))
figtitle = "MEG CAMCAN data"
#fig.suptitle(figtitle, fontsize=25)
classifiers=["lr", "lda", "svm", "rf"]

for ax_idx,ax in enumerate(axes.flat):
    ax.text(-0.1, 1.05, string.ascii_uppercase[ax_idx], transform=ax.transAxes, 
            size=20, weight='bold')
    if ax_idx == 0:
        data_distribution(pl, ax=ax, show=False)
    elif ax_idx < 5:
        metric_balance(pl, ax=ax, show=False, classifier="svm")

## Task 4 : MEG 2

In [ ]:
# generate random data
x, y, groups = gaussian_binary(n_samples_per_class=1500, n_groups=5, mean_distance=1)
# run the pipeline
pl_nsamples = Pipeline(
    x,
    y,
    groups,
    dataset_balance=np.linspace(0.1, 0.9, 25),
    classifiers=["svm"],# "rf"],
    metrics=["roc_auc", "accuracy", "f1", "balanced_accuracy"],
    n_permutations=0,
    n_init=1,
    dataset_size=(0.1, 0.33, 1)
)
pl_nsamples.evaluate()